In [1]:
#### !!!! IMPORTANT NOTE !!!! ####
# the following installs pysat on colab
# to install pysat locally run:
# "pip install python-sat[aiger,approxmc,cryptosat,pblib]"
# for more information see https://pysathq.github.io/installation/
!pip install python-sat[aiger,approxmc,cryptosat,pblib]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.0/74.0 kB 3.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 57.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.0/9.0 MB 48.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.7/2.7 MB 51.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 kB 3.4 MB/s eta 0:00:00
  Created wheel for pypblib: filename=pypblib-0.0.4-cp310-cp310-linux_x86_64.whl size=2973438 sha256=ee3b105193ee45e89251d93127825c5a034e34a7efafd251a7dff22a6f3ce609
  Stored in directory: /root/.cache/pip/wheels/a8/3d/9c/b980a09d6084eaeb9b336edbe20371c53c2550226daeee2025
Successfully built pypblib
  Attempting uninstall: bidict
    Found existing installation: bidict 0.23.1
    Uninstalling bidict-0.23.1:
      Successfully uninstalled bidict-0.23.1


In [2]:
from pysat.solvers import Cadical195
from pysat.formula import IDPool
from itertools import combinations
#from itertools import batched  # available for newer python versions, colab is only 3.10
from more_itertools import chunked
def batched(L,r): return list(chunked(L,r))

assignment = {
(1,2):3,
(2,4):1,
(2,5):9,
(2,6):5,
(3,3):8,
(3,8):6,
(4,1):8,
(4,5):6,
(5,1):4,
(5,4):8,
(5,9):1,
(6,5):2,
(7,2):6,
(7,7):2,
(7,8):8,
(8,4):4,
(8,5):1,
(8,6):9,
(8,9):5,
(9,8):7,
}


values = range(1,10) # [1,2,3,4,5,6,7,8,9]

# create dictionary for variables (map anything to 1,2,3,...)
vpool = IDPool()
# variables to indicate whether in row r, column c, the value is v
X = {(r,c,v):vpool.id() for r in values for c in values for v in values}

# Note: one can also use "X = lambda(r,c,v): vpool.id(r,c,v)"
# this allows to write X(r,c,v) (function call) instead of X[r,c,v] (dictionary)

cnf = []

# each field has one value
for r in values:
	for c in values:
		cnf.append([X[r,c,v] for v in values])
		for v1,v2 in combinations(values,2):
			cnf.append([-X[r,c,v1],-X[r,c,v2]])

# every value appears one per row
for r in values:
	for v in values:
		cnf.append([X[r,c,v] for c in values])

# every value appears one per column
for c in values:
	for v in values:
		cnf.append([X[r,c,v] for r in values])

# every value appears one per box
value_blocks = batched(values,3) # [1,...9] -> [1,2,3],[4,5,6],[7,8,9]
for v in values:
	for r_block in value_blocks:
		for c_block in value_blocks:
			cnf.append([X[r,c,v] for r in r_block for c in c_block])

# fix prescribed entries
for r,c in assignment:
	v = assignment[r,c]
	cnf.append([X[r,c,v]])

solver = Cadical195(bootstrap_with=cnf)

#ct=0
#for solution in solver.enum_models():
#	ct += 1
for ct,solution in enumerate(solver.enum_models()):
	print(f"solution #{ct+1}")
	for r in values:
		for c in values:
			for v in values:
				if X[r,c,v] in solution:
					print(f"{v}*" if (r,c) in assignment else f"{v} ",end=" ")
		print()
	if ct >= 2: break # stop after 3 solutions

solution #1
5  3* 4  6  7  8  9  1  2  
6  7  2  1* 9* 5* 3  4  8  
1  9  8* 3  4  2  5  6* 7  
8* 5  9  7  6* 1  4  2  3  
4* 2  6  8* 5  3  7  9  1* 
7  1  3  9  2* 4  8  5  6  
9  6* 1  5  3  7  2* 8* 4  
2  8  7  4* 1* 9* 6  3  5* 
3  4  5  2  8  6  1  7* 9  
